In [1]:
import numpy as np
import math
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d.art3d import Poly3DCollection
from scipy.interpolate import griddata
import meshpy.tet as tet
import plotly.graph_objects as go
import scipy as sc


In [18]:
'''Constant. SI unit'''
pi=math.pi
electron_charge=1.602176634*10**(-19)
vacuum_permitivity=8.8541878188*10**(-12)
relative_permitivity=1
reduced_planck_constant=6.62607015*10**(-34)/(2*pi)
electron_mass=9.1093837139*10**(-31)
eff_mass_hole=0.044
eff_mass_e=0.041


In [69]:
'''Defining shape and boundary. The shape is assumed to be a polyhedron with 2 hexagonal bases and the top is 50% the size of the bottom'''
unit_length=2*10**(-8)    #Unit length. In meters. 10^-8 is 10 nanometers.
a=1                  #Bottom radius. In unit length. Always put a<=1
tilt=0.5                #Top-to-bottom ratio. Always <=1
h=0.5                   #Height of the shape. Always put h<=1

In [ ]:
'''Simulation parameters. This part is used to change the parameter of the 3D mesh and the integration.'''
dV=0.01                                 #Change with caution. Small dV could increase accuracy but largely increase the time
integral_points=100000                  #Number of samples in Monte Carlo integral of Coulomb interaction
rng=np.random.default_rng(20092004)     #Random seed. Change to whatever lucky number you like. To my dear Autumn

In [83]:
'''Mesh generation. Don't touch this part if you don't really understand.'''
points=[(a,0,0),
        (a*1/2,a*np.sqrt(3)/2,0),
        (-a*1/2,a*np.sqrt(3)/2,0),
        (-a,0,0),
        (-a*1/2,-a*np.sqrt(3)/2,0),
        (a*1/2,-a*np.sqrt(3)/2,0),
        (tilt*a,0,h),
        (tilt*a*1/2,tilt*a*np.sqrt(3)/2,h),
        (-tilt*a*1/2,tilt*a*np.sqrt(3)/2,h),
        (-a*tilt,0,h),
        (-a*tilt*1/2,-a*tilt*np.sqrt(3)/2,h),
        (a*tilt*1/2,-a*tilt*np.sqrt(3)/2,h)]
facets=[
    [6,7,1,0],[7,8,2,1],[8,9,3,2],[9,10,4,3],[10,11,5,4],[11,6,0,5],[0,1,2,3,4,5],[6,7,8,9,10,11]
]
mesh_info=tet.MeshInfo()
mesh_info.set_points(points)
mesh_info.set_facets(facets)
mesh=tet.build(mesh_info,max_volume=dV)
mesh_points = np.array(mesh.points)
mesh_elements = np.array(mesh.elements)

face1=mesh_points[:,2]<=0
face2=mesh_points[:,2]>=h
face3=mesh_points[:,1]+np.sqrt(3)/2*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)<=0
face4=mesh_points[:,1]-np.sqrt(3)/2*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)>=0
face5=-np.sqrt(3)*mesh_points[:,0]+mesh_points[:,1]-np.sqrt(3)*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)>=0
face6=-np.sqrt(3)*mesh_points[:,0]+mesh_points[:,1]+np.sqrt(3)*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)<=0
face7=np.sqrt(3)*mesh_points[:,0]+mesh_points[:,1]-np.sqrt(3)*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)>=0
face8=np.sqrt(3)*mesh_points[:,0]+mesh_points[:,1]+np.sqrt(3)*a*(1-mesh_points[:,2]/h+tilt*mesh_points[:,2]/h)<=0
border=np.array([face1,face2,face3,face4,face5,face6,face7,face8]).any(axis=0)
mesh_border=mesh_points[border]
mesh_int=mesh_points[~border]

In [74]:
'''Initialize the global matrix'''
num_nodes=mesh_points.shape[0]
num_elements=mesh_elements.shape[0]
#Local basis
K_small=np.array([[2, 1, 1, 1],
                   [1, 2, 1, 1],
                   [1, 1, 2, 1],
                   [1, 1, 1, 2]]) / 120
#Initialize K matrix and M matrix
K=np.zeros((num_nodes,num_nodes))   #ui*uj
M=np.zeros((num_nodes,num_nodes))   #grad ui *grad uj
print(num_nodes,num_elements)



655 2074


In [75]:
'''Assemble the global matrix'''
#Assemble K matrix and M matrix

for element in mesh_elements:
    coords=mesh_points[element]
    
    x0=coords[0,0]
    y0=coords[0,1]
    z0=coords[0,2]
    
    x1=coords[1,0]
    y1=coords[1,1]
    z1=coords[1,2]
    
    x2=coords[2,0]
    y2=coords[2,1]
    z2=coords[2,2]
    
    x3=coords[3,0]
    y3=coords[3,1]
    z3=coords[3,2]
    
    jacob=np.array([[-x0 + x1, -x0 + x2, -x0 + x3], [-y0 + y1, -y0 + y2, -y0 + y3], [-z0 + z1, -z0 + z2, -z0 + z3]])
    det=np.abs(np.linalg.det(jacob)) 
    grad=np.linalg.inv([[x0,y0,z0,1],[x1,y1,z1,1],[x2,y2,z2,1],[x3,y3,z3,1]])[[0,1,2],:]
    M_small=np.dot(grad.T,grad)
    k_element=det*K_small
    m_element=det*M_small/6

    for m in range(4):
        for n in range(4):
            K[element[m],element[n]]+=k_element[m,n]
            M[element[m],element[n]]+=m_element[m,n]


In [76]:
'''Border condition.'''
for i in range(num_nodes):
    if border[i]:
        K[i,:]=0
        M[i,:]=0
        K[i,i]=1
        M[i,i]=1
        

           

In [77]:
'''Solving for eigenstate and eigenvalue'''
energy,wvfunc=sc.linalg.eig(M,K)

In [78]:
'''Finding ground state'''
state=np.argmin(energy[energy!=1])
ground=energy[state]
grnd_state=wvfunc[:,state]
print(ground)

(62.81396161363366+0j)


$\int\langle\Psi\vert\frac{1}{\vert\sqrt{\vec{r}_e-\vec{r}_h}\vert^2}\vert \Psi \rangle d^3\vec{r}$

In [79]:
'''Calculate the integral for 1/r potential'''
monte=rng.random(size=(2*integral_points,3))
monte[:,[0,1]]=monte[:,[0,1]]*2-1
func=griddata(mesh_points
               ,grnd_state,
               (monte[:,0],monte[:,1],monte[:,2]),
               method='linear')
func[np.isnan(func)]=0
sum1=0
sum2=0
for i in range(integral_points):
    sum1+=func[i]*func[i]*func[i+integral_points]*func[i+integral_points]/np.sqrt((monte[i,0]-monte[i+integral_points,0])**2
                   +(monte[i,1]-monte[i+integral_points,1])**2
                   +(monte[i,2]-monte[i+integral_points,2])**2)
    sum2+=func[i]*func[i]*func[i+integral_points]*func[i+integral_points]
sum=sum1/sum2
print(sum)

3.0617229484417283


In [80]:
'''Calculate the final binding energy'''
binding_energy=(reduced_planck_constant**2)/2*(1/(eff_mass_e*electron_mass)+1/(eff_mass_hole*electron_mass))*ground/(unit_length*unit_length)
+electron_charge**2/(4*pi*vacuum_permitivity*relative_permitivity)*sum/unit_length      #Energy in Joules
binding_energy_ev=binding_energy/electron_charge                                        #Energy in eV
print(binding_energy_ev)

(0.2819041845301549+0j)


In [67]:
'''Visualize'''
x_gr,y_gr,z_gr=np.meshgrid(np.linspace(-1,1,51),
                           np.linspace(-1,1,51),
                           np.linspace(0,1,41))
interpolated=griddata(mesh_points,
                      grnd_state,
                      (x_gr,y_gr,z_gr),
                      method='linear')
interpolated[np.isnan(interpolated)]=0
probability=interpolated.ravel()**2


In [68]:
fig = go.Figure(data=go.Volume(
    x=x_gr.ravel(),
    y=y_gr.ravel(),
    z=z_gr.ravel(),
    value=probability,
    isomin=0,
    isomax=0.15,
    opacity=0.1,
    surface_count=100,
    colorscale='plasma'
))
fig.add_trace(go.Scatter3d(
    x=mesh_points[:,0],
    y=mesh_points[:,1],
    z=mesh_points[:,2],
    mode='markers',
    marker=dict(
        size=1,
        color='black',
        opacity=1
    )
))
fig.update_layout(title='3D ground state probability distribution',
                  scene=dict(
                  xaxis=dict(
                      title=dict(
                          text='x (unit length)'
                      )
                  ),
                  yaxis=dict(
                      title=dict(
                          text='y (unit length)'
                      )
                  ),
                  zaxis=dict(
                      title=dict(
                          text='z (unit length)'
                      )
                  )),
                  width=800,
                  height=600,
                  autosize=False,
                  margin=dict(
    l=0,
    r=0
))
fig.show(width=800,height=600)